In [1]:
# Tratamiento de datos
# -----------------------------------------------------------------------
import pandas as pd

# Para visualización de datos
# -----------------------------------------------------------------------
import seaborn as sns
import matplotlib.pyplot as plt

# Para cargar los datos
# -----------------------------------------------------------------------
import pickle

# Para sistemas de recomendacion basados en cotenido
# -----------------------------------------------------------------------
from scipy.spatial.distance import pdist , squareform   # Para calcular la distancia entre puntos 

# Importamos nuestras funciones
# -----------------------------------------------------------------------
from src import soporte_sistemas_recomendacion as sr

# Configuración de pandas
# -----------------------------------------------------------------------
pd.set_option('display.max_columns', None)

# Sistema de recomendación colaborativo

Este tipo de sistema de recomendación sugiere artículos basándose en las preferencias de los usuarios y la relación entre artículos. Parte de la idea de que a las personas les gustan productos similares a los que ya disfrutan, así como artículos que son del agrado de personas con gustos parecidos.

Por ejemplo, si al usuario A le gustan Iron-Man, Batman y Spider-Man, y al usuario B le gustan Batman, Superman y Thor, es probable que en el futuro se recomiende la película Thor al usuario A, y la película Iron-Man al usuario B, ya que comparten intereses similares en películas.

Las interacciones anteriores entre usuarios y artículos se almacenan en una matriz llamada "matriz de interacción usuario-artículo", que se utiliza para generar recomendaciones personalizadas.

Existen dos enfoques comunes para crear sistemas de recomendación colaborativa:

- **Enfoque basado en memoria**: utiliza los datos de interacciones registradas entre usuarios y productos. Este método se enfoca en encontrar usuarios similares mediante algoritmos de similitud o correlación, y luego se calculan las recomendaciones basándose en el promedio ponderado de las calificaciones de esos usuarios cercanos.
  
- **Enfoque basado en modelos**: emplea algoritmos de aprendizaje automático para generar nuevas representaciones de usuarios y productos. Las recomendaciones se basan en las predicciones realizadas por el modelo.

Los enfoques basados en memoria se dividen en dos técnicas, que utilizan factores de filas y columnas para generar recomendaciones.

### Tipos de sistemas de recomendación colaborativa basados en memoria:

- **Usuario a usuario**: Se crea una matriz donde cada fila representa a un usuario y cada columna un producto. Se calculan las similitudes entre usuarios. Se identifican usuarios con gustos parecidos a un usuario determinado.  Se sugieren recomendaciones personalizadas basadas en esas similitudes.

- **Artículo a artículo**: Se identifica la relación entre los artículos y se recomiendan aquellos que han sido vistos con mayor frecuencia por diferentes usuarios. Este enfoque suele considerarse más eficaz que los sistemas basados en usuarios. Se crea una matriz en la que cada fila representa un artículo y cada columna corresponde a un usuario. Se calculan las similitudes entre los artículos. Se sugieren artículos a los usuarios basándose en la frecuencia con la que han sido vistos.

In [2]:
# cargamos los datos
df_rat = pd.read_csv('datos/movie_ratings42.csv').set_index('Movie')

# antes de nada tenemos que transponer el conjunto de datos 
df_rat = df_rat.T
df_rat.head()

Movie     Aquaman  Avengers: Infinity War  Black Panther  Bohemian Rhapsody  \
Brandon         4                       2              5                  2   
Emily           1                       5              2                  3   
Cleo            2                       2              5                  4   
Rusty           2                       5              1                  4   
Samantha        2                       5              1                  1   

Movie     Deadpool 2  Fantastic Beasts: The Crimes of Grindelwald  \
Brandon            3                                            5   
Emily              2                                            4   
Cleo               4                                            1   
Rusty              5                                            2   
Samantha           1                                            5   

Movie     Incredibles 2  Jurassic World: Fallen Kingdom  \
Brandon               4                               2   
Emily                 2                               3   
Cleo                  3                               5   
Rusty                 4                               4   
Samantha              4                               5   

Movie     Mission: Impossible – Fallout  Venom  
Brandon                               5      4  
Emily                                 5      1  
Cleo                                  4      4  
Rusty                                 3      5  
Samantha                              2      2

# Calculo de Distancias

El cálculo de distancias es una fase fundamental en muchas áreas de la ciencia de datos, como el clustering, los sistemas de recomendación y el análisis de similitud. A continuación, hablaremos de dos herramientas clave de la biblioteca `scipy` para calcular y manejar distancias: `pdist` y `squareform`.


## pdist: Cálculo de distancias entre pares

La función `pdist` de `scipy.spatial.distance` calcula las distancias entre todos los pares de filas en una matriz de puntos. Es especialmente útil para comparar similitudes o diferencias entre múltiples elementos en un espacio multidimensional. Su sintaxis básica es:


```python
from scipy.spatial.distance import pdist

pdist(X, metric='euclidean')
```

Donde:

- `X` (array-like): Matriz de entrada donde:

	- Cada fila representa un punto en un espacio n-dimensional.

	- Cada columna representa una dimensión o característica.

- `metric` (opcional):Define la métrica utilizada para calcular la distancia Las métricas más comunes son: 

	- 'euclidean': Distancia euclidiana (por defecto).

	- 'cosine': Similitud del coseno (usada frecuentemente en texto y vectores densos).

	- 'manhattan': Distancia Manhattan o L1.

	- 'correlation': Distancia basada en correlación.


Devuelve un vector 1D que contiene las distancias entre todos los pares de filas en la matriz de entrada, en un formato compacto. Este vector tiene un tamaño de $frac{n \times (n - 1)}{2}$, donde (n) es el número de filas en la matriz.


## squareform: Matriz cuadrada de distancias

La función squareform convierte el vector 1D resultante de pdist en una matriz cuadrada de distancias o viceversa. Es útil para:


- Aunque el formato compacto de pdist es eficiente, puede ser difícil de interpretar.

- Una matriz cuadrada permite visualizar fácilmente las distancias entre puntos:

- Las filas y columnas representan los puntos.

- La celda ((i, j)) contiene la distancia entre el punto (i) y (j).

Su sintaxis básica es:

```python
from scipy.spatial.distance import squareform

squareform(X)
```

Donde:
- `X` (array-like):


Devuelve una matriz cuadrada si la entrada es un vector compacto, o un vector compacto si la entrada es una matriz cuadrada.

In [3]:
# calculamos las distancias usando squareform
distancias_square = squareform(pdist(df_rat, 'euclidean'))   

# pertenecen al intervalo (0, 1) de esta forma conseguimos que los valores este acotados 
similitud_square = 1/(1 + distancias_square)
similitud_square[:10]

array([[1.        , 0.1310058 , 0.14285714, 0.11881849, 0.11787845],
       [0.1310058 , 1.        , 0.12613198, 0.13507811, 0.16396078],
       [0.14285714, 0.12613198, 1.        , 0.15225881, 0.10815241],
       [0.11881849, 0.13507811, 0.15225881, 1.        , 0.12973191],
       [0.11787845, 0.16396078, 0.10815241, 0.12973191, 1.        ]])

In [4]:
df_similitud = pd.DataFrame(similitud_square, columns=df_rat.T.columns, index=df_rat.T.columns)
df_similitud

Brandon     Emily      Cleo     Rusty  Samantha
Brandon   1.000000  0.131006  0.142857  0.118818  0.117878
Emily     0.131006  1.000000  0.126132  0.135078  0.163961
Cleo      0.142857  0.126132  1.000000  0.152259  0.108152
Rusty     0.118818  0.135078  0.152259  1.000000  0.129732
Samantha  0.117878  0.163961  0.108152  0.129732  1.000000

# Caso práctico 2

Hemos hecho un ejemplo sencillo para un conjunto de datos pequeño, ahora toca poner a prueba los conceptos aprendidos con un conjunto de datos más grande. 

In [5]:
# cargamos lso datos
with open('datos/metadata_clean.pkl', 'rb') as archivo:
    df = pickle.load(archivo)
df.head()


movieId  tmdbId  imbd_mean  imbd_count  adult      budget  \
0        1     862   3.888157       66008  False  30000000.0   
1        2    8844   3.236953       26060  False  65000000.0   
2        3   15602   3.175550       15497  False         0.0   
3        4   31357   2.875713        2981  False  16000000.0   
4        5   11862   3.079565       15258  False         0.0   

                                              genres     id    imdb_id  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...    862  tt0114709   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   8844  tt0113497   
2  [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...  15602  tt0113228   
3  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...  31357  tt0114885   
4                     [{'id': 35, 'name': 'Comedy'}]  11862  tt0113041   

  original_language               original_title  \
0                en                    Toy Story   
1                en                      Jumanji   
2                en             Grumpier Old Men   
3                en            Waiting to Exhale   
4                en  Father of the Bride Part II   

                                            overview  popularity  \
0  Led by Woody, Andy's toys live happily in his ...   21.946943   
1  When siblings Judy and Peter discover an encha...   17.015539   
2  A family wedding reignites the ancient feud be...   11.712900   
3  Cheated on, mistreated and stepped on, the wom...    3.859495   
4  Just when George Banks has recovered from his ...    8.387519   

                                production_companies  \
0     [{'name': 'Pixar Animation Studios', 'id': 3}]   
1  [{'name': 'TriStar Pictures', 'id': 559}, {'na...   
2  [{'name': 'Warner Bros.', 'id': 6194}, {'name'...   
3  [{'name': 'Twentieth Century Fox Film Corporat...   
4  [{'name': 'Sandollar Productions', 'id': 5842}...   

                                production_countries release_date  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
1  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-15   
2  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-22   
3  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-12-22   
4  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-02-10   

       revenue  runtime                                   spoken_languages  \
0  373554033.0     81.0           [{'iso_639_1': 'en', 'name': 'English'}]   
1  262797249.0    104.0  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...   
2          0.0    101.0           [{'iso_639_1': 'en', 'name': 'English'}]   
3   81452156.0    127.0           [{'iso_639_1': 'en', 'name': 'English'}]   
4   76578911.0    106.0           [{'iso_639_1': 'en', 'name': 'English'}]   

     status                                            tagline  \
0  Released                                                NaN   
1  Released          Roll the dice and unleash the excitement!   
2  Released  Still Yelling. Still Fighting. Still Ready for...   
3  Released  Friends are the people who let you be yourself...   
4  Released  Just When His World Is Back To Normal... He's ...   

                         title  video  \
0                    Toy Story  False   
1                      Jumanji  False   
2             Grumpier Old Men  False   
3            Waiting to Exhale  False   
4  Father of the Bride Part II  False   

                                            keywords  \
0  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   
1  [{'id': 10090, 'name': 'board game'}, {'id': 1...   
2  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...   
3  [{'id': 818, 'name': 'based on novel'}, {'id':...   
4  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...   

                                                cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   
1  [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2  [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3  [{'cast_id': 1, 'chara

In [6]:
# cargamos el segundo conjunto de datos que vamos a necesitar
with open('datos/ratings_merge.pkl', 'rb') as archivo:
    ratings_df = pickle.load(archivo)
ratings_df.head()


userId  movieId  rating   timestamp  imdbId  tmdbId
0       1      110     1.0  1425941529  112573     197
1      11      110     3.5  1231676989  112573     197
2      22      110     5.0  1111937009  112573     197
3      24      110     5.0   979870012  112573     197
4      29      110     3.0  1044020005  112573     197

In [7]:
# vamos a fusionar los dos conjuntos de datos
metadata_final = df.merge(ratings_df, left_on='id', right_on='tmdbId')
metadata_final.head()

movieId_x  tmdbId_x  imbd_mean  imbd_count  adult      budget  \
0          1       862   3.888157       66008  False  30000000.0   
1          1       862   3.888157       66008  False  30000000.0   
2          1       862   3.888157       66008  False  30000000.0   
3          1       862   3.888157       66008  False  30000000.0   
4          1       862   3.888157       66008  False  30000000.0   

                                              genres   id    imdb_id  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862  tt0114709   
1  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862  tt0114709   
2  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862  tt0114709   
3  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862  tt0114709   
4  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...  862  tt0114709   

  original_language original_title  \
0                en      Toy Story   
1                en      Toy Story   
2                en      Toy Story   
3                en      Toy Story   
4                en      Toy Story   

                                            overview  popularity  \
0  Led by Woody, Andy's toys live happily in his ...   21.946943   
1  Led by Woody, Andy's toys live happily in his ...   21.946943   
2  Led by Woody, Andy's toys live happily in his ...   21.946943   
3  Led by Woody, Andy's toys live happily in his ...   21.946943   
4  Led by Woody, Andy's toys live happily in his ...   21.946943   

                             production_companies  \
0  [{'name': 'Pixar Animation Studios', 'id': 3}]   
1  [{'name': 'Pixar Animation Studios', 'id': 3}]   
2  [{'name': 'Pixar Animation Studios', 'id': 3}]   
3  [{'name': 'Pixar Animation Studios', 'id': 3}]   
4  [{'name': 'Pixar Animation Studios', 'id': 3}]   

                                production_countries release_date  \
0  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
1  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
2  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
3  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   
4  [{'iso_3166_1': 'US', 'name': 'United States o...   1995-10-30   

       revenue  runtime                          spoken_languages    status  \
0  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   
1  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   
2  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   
3  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   
4  373554033.0     81.0  [{'iso_639_1': 'en', 'name': 'English'}]  Released   

  tagline      title  video  \
0     NaN  Toy Story  False   
1     NaN  Toy Story  False   
2     NaN  Toy Story  False   
3     NaN  Toy Story  False   
4     NaN  Toy Story  False   

                                            keywords  \
0  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   
1  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   
2  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   
3  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   
4  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...   

                                                cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   
1  [{'cast_id': 14, 'character': 'Woody (voice)',...   
2  [{'cast_id': 14, 'character': 'Woody (voice)',...   
3  [{'cast_id': 14, 'character': 'Woody (voice)',...   
4  [{'cast_id': 14, 'character': 'Woody (voice)',...   

                                                crew  \
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...   
1  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...   
2  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...   
3  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...   
4  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...   

                                                tags  \
0  animation comedy family pixar animation studio...   
1  a

In [8]:
# seleccionamos las columnas de interés y renombramos el nombre de las columnas
df_collab = metadata_final[["userId","id","title","rating"]]
df_collab.rename(columns={"id":"movieId"}, inplace = True)
df_collab.head()

/var/folders/gq/ms0v5g8s3tngswn6ym0ddcc00000gp/T/ipykernel_2051/2488508858.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_collab.rename(columns={"id":"movieId"}, inplace = True)


userId  movieId      title  rating
0       8      862  Toy Story     4.0
1       9      862  Toy Story     4.5
2      12      862  Toy Story     4.0
3      20      862  Toy Story     4.0
4      24      862  Toy Story     4.0

In [ ]:
# aplicamos la funcion para filtrar los datos
df_collab = sr.filter_data(df_collab)
df_collab.head()

userId  movieId            title  rating
203          741      862        Toy Story     4.5
233          836      862        Toy Story     3.5
505         1846      862        Toy Story     3.5
527         1932      862        Toy Story     3.5
687         2531      862        Toy Story     3.5
...          ...      ...              ...     ...
26136482  248894   126889  Alien: Covenant     2.0
26136488  255904   126889  Alien: Covenant     3.5
26136490  259495   126889  Alien: Covenant     3.5
26136506  267799   126889  Alien: Covenant     3.0
26136507  268356   126889  Alien: Covenant     2.0

[1555863 rows x 4 columns]

In [ ]:
# pivitamos la tabla
userRatings = df_collab.pivot_table(index=['userId'],columns=['title'],values='rating').fillna(0)
userRatings.head()


title   'night, Mother  (500) Days of Summer  ...And Justice for All   10  \
userId                                                                      
741                0.0                   0.0                     0.0  0.0   
836                0.0                   4.5                     0.0  0.0   
1846               0.0                   0.0                     0.0  0.0   
1932               0.0                   0.0                     0.0  0.0   
2520               0.0                   3.5                     0.0  0.0   
...                ...                   ...                     ...  ...   
270071             0.0                   3.5                     0.0  0.0   
270123             3.0                   2.0                     4.5  3.0   
270213             0.0                   0.0                     0.0  2.0   
270654             0.0                   3.5                     0.0  0.0   
270887             0.0                   0.0                     0.0  0.0   

title   10 Cloverfield Lane  10 Items or Less  10 Things I Hate About You  \
userId                                                                      
741                     0.0               0.0                         3.5   
836                     0.0               0.0                         5.0   
1846                    0.0               0.0                         3.0   
1932                    0.0               0.0                         2.0   
2520                    0.0               0.0                         0.0   
...                     ...               ...                         ...   
270071                  3.5               0.0                         2.5   
270123                  3.5               2.5                         0.0   
270213                  0.0               0.0                         2.0   
270654                  3.0               0.0                         0.0   
270887                  5.0               0.0                         0.0   

title   10,000 BC  100 Girls  101 Dalmatians  101 Reykjavik  102 Dalmatians  \
userId                                                                        
741           3.0        0.0             3.0            0.0             0.0   
836           3.0        0.0             2.5            0.0             2.5   
1846          2.5        0.0             2.5            0.0             0.0   
1932          1.0        0.0             0.0            0.0             0.0   
2520          0.0        0.0             0.0            0.0             0.0   
...           ...        ...             ...            ...             ...   
270071        0.0        0.0             0.0            0.0             0.0   
270123        0.0        2.0             0.0            0.0             0.0   
270213        0.0        0.0             3.0            0.0             4.0   
270654        0.0        0.0             0.0            0.0             0.0   
270887        1.0        0.0             1.0            0.0             1.5   

title   11:14  12 Angry Men  12 Years a Slave  127 Hours  13 Assassins  \
userId                                                                   
741       0.0          4.00               4.0        0.0           0.0   
836       0.0          0.00               4.0        0.0           0.0   
1846      0.0          5.00               5.0        3.0           3.5   
1932      0.0          0.00               0.0        0.0           0.0   
2520      0.0          0.00               0.0        0.0           0.0   
...       ...           ...               ...        ...           ...   
270071    0.0          3.50               3.5        3.5           0.0   
270123    4.5          4.25               3.5        4.0           0.0   
270213    0.0          5.00               0.0        0.0           0.0   
270654    0.0          4.00               0.0        3.5           0.0   
270887    3.0          1.00               5.0        4.0           0.0   

title

In [13]:
# calculamos la matriz de correlacion
matr_corre = userRatings.corr(method='pearson')
matr_corre.head()

title                   'night, Mother  (500) Days of Summer  \
title                                                          
'night, Mother                1.000000             -0.033860   
(500) Days of Summer         -0.033860              1.000000   
...And Justice for All        0.248888             -0.068312   
10                            0.148627             -0.101621   
10 Cloverfield Lane          -0.070919              0.295243   

title                   ...And Justice for All        10  10 Cloverfield Lane  \
title                                                                           
'night, Mother                        0.248888  0.148627            -0.070919   
(500) Days of Summer                 -0.068312 -0.101621             0.295243   
...And Justice for All                1.000000  0.319397            -0.063581   
10                                    0.319397  1.000000            -0.120016   
10 Cloverfield Lane                  -0.063581 -0.120016             1.000000   

title                   10 Items or Less  10 Things I Hate About You  \
title                                                                  
'night, Mother                 -0.010042                   -0.075335   
(500) Days of Summer            0.173451                    0.159983   
...And Justice for All         -0.003272                   -0.052021   
10                              0.001994                   -0.049845   
10 Cloverfield Lane             0.039947                    0.023387   

title                   10,000 BC  100 Girls  101 Dalmatians  101 Reykjavik  \
title                                                                         
'night, Mother          -0.062723  -0.048398        0.050160       0.030104   
(500) Days of Summer     0.124456   0.162101       -0.024905       0.016632   
...And Justice for All  -0.113947  -0.027271        0.041327      -0.018574   
10                      -0.099354   0.001329        0.020257       0.019230   
10 Cloverfield Lane      0.161343   0.083424       -0.013555      -0.049880   

title                   102 Dalmatians     11:14  12 Angry Men  \
title                                                            
'night, Mother                0.026620 -0.048653      0.049600   
(500) Days of Summer         -0.018824  0.183682      0.034800   
...And Justice for All        0.015539  0.037341      0.182702   
10                            0.053483  0.010577      0.031689   
10 Cloverfield Lane          -0.012716  0.154910      0.043410   

title                   12 Years a Slave  127 Hours  13 Assassins  13 Ghosts  \
title                                                                          
'night, Mother                 -0.066439  -0.099574     -0.042703   0.057094   
(500) Days of Summer            0.358724   0.467703      0.208972  -0.096362   
...And Justice for All         -0.056528  -0.048114     -0.061744   0.034936   
10                             -0.104092  -0.151259     -0.089032   0.109266   
10 Cloverfield Lane             0.416688   0.336214      0.152636   0.003803   

title                   13 Going on 30  \
title                                    
'night, Mother               -0.041524   
(500) Days of Summer          0.218412   
...And Justice for All        0.023403   
10                           -0.007312   
10 Cloverfield Lane           0.076859   

title                   13 Hours: The Secret Soldiers of Benghazi  13 Tzameti  \
title                                                                           
'night, Mother                                          -0.013170   -0.031011   
(500) Days of Summer                                     0.213727    0.135915   
...And Justice for All                                   0.014133    0.005771   
10                                                      -0.022945    0.016705   
10 Cloverfield Lane                                      0.379447    0.050750   

title                       1408  149

In [14]:

nombre_movie = "Pulp Fiction"
rating = 5

similar_ratings = matr_corre[nombre_movie]*(rating-2.5)
recommendacion = similar_ratings.sort_values(ascending=False)

# printemoas la recomendacion
print(recommendacion[1:11].sort_values(ascending=False))

title
Reservoir Dogs       1.427877
Jackie Brown         1.146554
GoodFellas           1.144715
Kill Bill: Vol. 1    1.069461
Fargo                1.043732
Taxi Driver          1.007184
L.A. Confidential    0.972063
Kill Bill: Vol. 2    0.966756
American Beauty      0.959837
Trainspotting        0.957439
Name: Pulp Fiction, dtype: float64
